# Анализ пространственных данных. Домашнее задание №2

Мягкий дедлайн: __4 ноября 2020 г. 23:59__

Жесткий дедлайн (со штрафом в _50%_ от количества набранных вами за ДЗ баллов): __5 ноября 2020 г. 08:59__

Визуализация "чего-либо" __без__ выполненного основного задания оценивается в __0 баллов__

ФИО: `Черников Дмитрий Владимирович`

Группа: `MADE-ML-12`

## Задание №1. Горячая точка (алгоритм - 10 баллов, визуализация - 10 баллов).

Генерируйте рандомные точки на планете Земля до тех пор, пока не попадете на территорию ``Афганистана``

1. Вы можете использовать функции принадлжености точки полигону и расстояния от точки до полигона (в метрах)
2. Предложите не наивный алгоритм поиска (генерировать __напрямую__ точку из полигона границ Афганистана __запрещено__)

In [1]:
import pandas as pd
import geopandas as gpd
import numpy as np

import folium

from shapely.geometry import Point, LineString, Polygon, MultiPolygon, mapping
from random import seed, uniform


__Импортируем полигон Афганистана__

'Afghanistan.geojson' экспортировал через Overpass: https://overpass-turbo.eu/s/ZHh \
`rel["ISO3166-1"="AF"];
 out geom;`

In [2]:
df = gpd.read_file('Afghanistan.geojson')
geom = df['geometry']
geom

0    POLYGON ((73.89205 36.87980, 73.89218 36.87877...
1                            POINT (69.17768 34.52601)
2                            POINT (66.23851 33.76801)
Name: geometry, dtype: geometry

Объект `geom` содержит три объекта - непосредственно polygon и две точки - столицу (Кабул) и центр полигона.\
У `gpd` порядок координат `lon`, `lat`, у `folium` - `lat`, `lon`, здесь мы переставим координаты,\
чтобы генерировать случайные точки и отображать их в `folium`

In [3]:
x, y = geom[0].exterior.coords.xy
afghanistan_area = Polygon(list(zip(list(y), list(x))))

__1. Случайный поиск точки в Афганистане__

In [4]:
def random_point():
    return Point(uniform(-90, 90), uniform(-180, 180))


seed()

n = 0
pt = random_point()
while not pt.within(afghanistan_area):
    n += 1
    pt = random_point()
    if n > 1000:
        raise ValueError(f"Too many random hops: {n}")

print(f"Random hops = {n}")
print(f"Random point: ({pt.x}, {pt.y})")

Random hops = 537
Random point: (32.786774676720526, 61.729103613142996)


__2. Не наивный алгоритм поиска:__
- 1) генегируем случайную точку `pt`
- 2) считаем расстояние `distance = pt.distance(poly)`
- 3) на каждом шаге считаем `d = pt.distance(poly)`
- 4) если расстояние `d` меньше значения `EPS`
     увеличиваем `d` на `distance / 2` и уменьшаем `distance` в два раза
- 5) выбираем ближайшую из четырех точек\
`[[pt.x + d, pt.y], [pt.x - d, pt.y], [pt.x, pt.y + d], [pt.x, pt.y - d]]`
- 6) если точка внутри полигона, то стоп, иначе шаг (3)

In [5]:
def point_search(pt, poly, distance, eps):
    d = pt.distance(poly)
    if d < eps:
        d += distance / 2
        distance /= 2
    a = [[pt.x + d, pt.y],
         [pt.x - d, pt.y],
         [pt.x, pt.y + d],
         [pt.x, pt.y - d]]

    fd = lambda x: Point(x[0], x[1]).distance(poly)
    idx = np.argmin(list(map(fd, a)))
    return Point(a[idx][0], a[idx][1]), distance

EPS = 0.01

n = 0
pt = random_point()

center = [geom[2].y, geom[2].x]
afghanistan_map = folium.Map(width='75%',height='75%',location=center,zoom_start=3)
folium.GeoJson(geom[0]).add_to(afghanistan_map)

folium.Marker(
    location=(pt.x, pt.y),
    popup=f"Point{n}",
    icon=folium.Icon(color='blue')
).add_to(afghanistan_map)

distance = pt.distance(afghanistan_area)
while not pt.within(afghanistan_area):
    n += 1
    pt, distance = point_search(pt, afghanistan_area, distance, EPS)
    
    color = 'orange'
    if pt.within(afghanistan_area):
        color = 'red'
    
    folium.Marker(
        location=(pt.x, pt.y),
        popup=f"Point{n}",
        icon=folium.Icon(color=color)
    ).add_to(afghanistan_map)

    
TASK2_POINT = pt      
print(f"Point search steps = {n}")
print(f"Found point: ({pt.x}, {pt.y})")


afghanistan_map

Point search steps = 13
Found point: (36.893057165933705, 67.38220062480286)


## Задание №2. Качество жизни (20 баллов).

Для измерения показателя качества жизни в точке, найденной в предыдущем задании, вам необходимо рассчитать следующую сумму расстояний (в метрах):

1. Расстояние от точки до 5 ближайших __*__ банкоматов, находящихся в стране с наибольшим количеством объектов жилой недвижимости
2. Расстояние от точки до 5 ближайших школ, находящихся в стране с наибольшим количеством аптек в столице
3. Расстояние от точки до 5 ближайших кинотеатров, наодящихся в стране с самым большим отношением числа железнодорожных станций к автобусным остановкам в южной части __**__

__*__ При поиске _N_ ближайших объектов обязательно использовать ``R-tree``

__**__ Южной частью страны является территория, находящаяся к югу от множества точек, равноудаленных от самой северной и самой южной точек страны

In [6]:
import pandas as pd
import geopandas as gpd
import numpy as np

import folium

from shapely.geometry import Point, LineString, Polygon, MultiPolygon, mapping
from OSMPythonTools.overpass import Overpass, overpassQueryBuilder
from OSMPythonTools.nominatim import Nominatim
from haversine import haversine, Unit
from rtree import index


overpass = Overpass()
nominatim = Nominatim()


__1.1. Собираем AreaId стран, оставляем страны у которых AreaId заканчивается на 0__

In [7]:
query = '\
rel["ISO3166-1"]\
[admin_level=2]\
[type=boundary]\
[boundary=administrative];\
out meta;'

result = overpass.query(query)

country_ids = []
country_names = []
for elem in result.elements():
    name = elem.tags()['name:en']
    areaId = nominatim.query(name).areaId()
    if areaId % 10 == 0:
        country_ids.append(areaId)
        country_names.append(name)

list(zip(country_ids, country_names))

[(3600059470, 'Brazil'),
 (3600079510, 'Estonia'),
 (3600080500, 'Australia'),
 (3600088210, 'Eswatini'),
 (3600184640, 'Bangladesh'),
 (3600184840, 'Syria'),
 (3600192780, 'Liberia'),
 (3600192790, 'Central African Republic'),
 (3600192800, 'Ethiopia'),
 (3600192830, 'Cameroon'),
 (3600195270, 'Tanzania'),
 (3600195290, 'Malawi'),
 (3600196240, 'Uzbekistan'),
 (3600287670, 'Honduras'),
 (3600295480, 'Portugal'),
 (3600364110, 'Azerbaijan'),
 (3600535790, 'Comoros'),
 (3600535880, 'São Tomé and Príncipe'),
 (3600536900, 'Antigua and Barbuda'),
 (3600036990, 'Monaco'),
 (3602088990, 'Kosovo'),
 (3602103120, 'Brunei'),
 (3602186600, 'Tokelau'),
 (3602978650, 'Norway')]

__1.2. Считаем объекты жилой недвижимости: https://wiki.openstreetmap.org/wiki/Key:building__

In [15]:
accomodations = ['apartments', 'bungalow', 'cabin', 'detached', 'dormitory', 'farm', 'ger', 'hotel', \
                 'house', 'houseboat', 'residential', 'semidetached_house', 'static_caravan', 'terrace']

country_accomodations = []
for areaId in country_ids:
    counter = 0
    for building in accomodations:
        query = overpassQueryBuilder(area=areaId, 
                                     elementType=['area','relation'],
                                     selector=f'"building"="{building}"', 
                                     out='count')
        result = overpass.query(query, timeout=3600)
        counter += result.countElements()

    country_accomodations.append(counter)

list(zip(country_names, country_accomodations))

[('Brazil', 1366840),
 ('Estonia', 1358316),
 ('Australia', 1358652),
 ('Eswatini', 1358309),
 ('Bangladesh', 1358346),
 ('Syria', 1358311),
 ('Liberia', 1358310),
 ('Central African Republic', 1358305),
 ('Ethiopia', 1358329),
 ('Cameroon', 1358316),
 ('Tanzania', 1358804),
 ('Malawi', 1358322),
 ('Uzbekistan', 1358486),
 ('Honduras', 1358307),
 ('Portugal', 1358865),
 ('Azerbaijan', 1358309),
 ('Comoros', 1358305),
 ('São Tomé and Príncipe', 1358305),
 ('Antigua and Barbuda', 1358309),
 ('Monaco', 1358305),
 ('Kosovo', 1358525),
 ('Brunei', 1358521),
 ('Tokelau', 1358516),
 ('Norway', 1358733)]

Страна с наибольшим количество жилой недвижимости

In [16]:
imax = np.argmax(country_accomodations)
areaId = country_ids[imax]
print(f"Country with max accomodations: {country_names[imax]} ({areaId})")


Country with max accomodations: Brazil (3600059470)


__1.3 Выберем банкоматы в стране с наибольшим количеством жилой недвижимости\
и проиндексируем их с помощью R-tree__

In [10]:
query = f'\
node(area:{areaId})["amenity"="atm"];\
out geom;'

result = overpass.query(query, timeout=3600)

EPS = 0.000001
idx = index.Rtree()

atm_ids = []
atm_points = []
for i in range(result.countElements()):
    atm_id = result.elements()[i].id()
    atm_ids.append(atm_id)
    
    lon = result.elements()[i].geometry().coordinates[0]
    lat = result.elements()[i].geometry().coordinates[1]
    idx.insert(atm_id, (lon - EPS, lat + EPS, lon + EPS, lat + EPS))
    
    atm_points.append(Point(lat, lon))

atm_df = gpd.GeoDataFrame(zip(atm_ids, atm_points,[0] * len(atm_ids)), 
                          columns=['ids','geometry','distance'],
                          geometry='geometry',
                          crs={'init': 'epsg:4326'})
atm_df

C:\ProgramData\Anaconda3\envs\made-geo\lib\site-packages\pyproj\crs\crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))


ids                     geometry  distance
0      315000482  POINT (-20.65244 -40.49757)         0
1      315000484  POINT (-20.67034 -40.49837)         0
2      315000504  POINT (-20.32064 -40.35169)         0
3      315000513  POINT (-20.31245 -40.28785)         0
4      320218260  POINT (-19.95696 -44.06233)         0
...          ...                          ...       ...
1327  8041248414  POINT (-29.98046 -50.13230)         0
1328  8045189417  POINT (-23.01573 -45.55085)         0
1329  8070292900   POINT (-5.76134 -35.25241)         0
1330  8070292903   POINT (-5.75737 -35.24393)         0
1331  8070292904   POINT (-5.74731 -35.22672)         0

[1332 rows x 3 columns]

__1.4. Найдем ближайшие банкоматы и расстояние до них для точки из Афганистана__

In [11]:
nearest_ids = list(idx.nearest((TASK2_POINT.y, TASK2_POINT.x, TASK2_POINT.y, TASK2_POINT.x), 5))

atm_nearest = atm_df.loc[atm_df['ids'].isin(nearest_ids)]
for i in atm_nearest.index :
    atm_pt = atm_nearest.loc[i, 'geometry']
    d = haversine((TASK2_POINT.x, TASK2_POINT.y), (atm_pt.x, atm_pt.y))
    atm_nearest.loc[i, 'distance'] = d
    
print("Пять ближайших к точке в Афганистан банкоматов в Бразилии")
atm_nearest


Пять ближайших к точке в Афганистан банкоматов в Бразилии


C:\ProgramData\Anaconda3\envs\made-geo\lib\site-packages\pandas\core\indexing.py:1765: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  isetter(loc, value)


ids                    geometry      distance
335  2600419328  POINT (-3.84060 -32.41094)  11134.316477
336  2600419329  POINT (-3.84143 -32.41100)  11134.376531
337  2600419340  POINT (-3.85650 -32.42859)  11136.943083
338  2600419341  POINT (-3.85654 -32.42859)  11136.945459
343  2601191548  POINT (-3.84935 -32.42589)  11136.226699

__2.1. Собираем AreaId столиц, для стран у которых AreaId заканчивается на 0__

In [12]:
subquery = f'\
[admin_level=2]\
[type=boundary]\
[boundary=administrative];\
(node(r:"admin_centre") -> .a;);\
out meta;'

capital_ids = []
capital_names = []

for areaId in country_ids:
    query = f'rel(area:{areaId})' + subquery;
    result = overpass.query(query, timeout=3600)
    name = result.elements()[0].tags()['name:en']
    areaId = nominatim.query(name).areaId()
    capital_ids.append(areaId)
    capital_names.append(name)
        
# 'Canberra'
capital_ids[2] = 21674637
# 'Mbabane'
capital_ids[3] = 243837793
# 'Fakaofo'
capital_ids[22] = 3168342084

list(zip(capital_ids, capital_names))

[(3600059470, 'Brasília'),
 (3602164745, 'Tallinn'),
 (21674637, 'Canberra'),
 (243837793, 'Mbabane'),
 (3610249594, 'Dhaka'),
 (3600186228, 'Damascus'),
 (3609319970, 'Monrovia'),
 (3607322726, 'Bangui'),
 (3601707699, 'Addis Ababa'),
 (3602746229, 'Yaounde'),
 (3601600774, 'Dodoma'),
 (3607345524, 'Lilongwe'),
 (3602216724, 'Tashkent'),
 (3603850824, 'Tegucigalpa'),
 (3605400890, 'Lisbon'),
 (3602415335, 'Baku'),
 (3600198859, 'Moroni'),
 (3609377730, 'São Tomé'),
 (3602805426, "St. John's"),
 (3600036990, 'Monaco'),
 (3602728438, 'Belgrade'),
 (3608748136, 'Bandar Seri Begawan'),
 (3168342084, 'Fakaofo'),
 (3600406091, 'Oslo')]

__2.2. Для каждой столицы считаем количество аптек__

In [17]:
capital_pharmacies = []
for areaId in capital_ids:
    query = overpassQueryBuilder(area=areaId, 
                                 elementType=['area','rel','node','way'],
                                 selector=f'"amenity"="pharmacy"', 
                                 out='count')
    result = overpass.query(query, timeout=3600)
    capital_pharmacies.append(result.countElements())

list(zip(capital_names, capital_pharmacies))

[('Brasília', 41304),
 ('Tallinn', 32509),
 ('Canberra', 32427),
 ('Mbabane', 32427),
 ('Dhaka', 32427),
 ('Damascus', 32429),
 ('Monrovia', 32430),
 ('Bangui', 32430),
 ('Addis Ababa', 32591),
 ('Yaounde', 32575),
 ('Dodoma', 32447),
 ('Lilongwe', 32437),
 ('Tashkent', 33290),
 ('Tegucigalpa', 32588),
 ('Lisbon', 32722),
 ('Baku', 32612),
 ('Moroni', 32427),
 ('São Tomé', 32427),
 ("St. John's", 32441),
 ('Monaco', 32439),
 ('Belgrade', 32737),
 ('Bandar Seri Begawan', 32431),
 ('Fakaofo', 32427),
 ('Oslo', 32556)]

Страна с наибольшим количество аптек в столице

In [18]:
imax = np.argmax(capital_pharmacies)
areaId = country_ids[imax]
print(f"Country with max pharmacies in the capital: {country_names[imax]} ({areaId})")
list(zip(capital_names, capital_pharmacies))

Country with max pharmacies in the capital: Brazil (3600059470)


[('Brasília', 41304),
 ('Tallinn', 32509),
 ('Canberra', 32427),
 ('Mbabane', 32427),
 ('Dhaka', 32427),
 ('Damascus', 32429),
 ('Monrovia', 32430),
 ('Bangui', 32430),
 ('Addis Ababa', 32591),
 ('Yaounde', 32575),
 ('Dodoma', 32447),
 ('Lilongwe', 32437),
 ('Tashkent', 33290),
 ('Tegucigalpa', 32588),
 ('Lisbon', 32722),
 ('Baku', 32612),
 ('Moroni', 32427),
 ('São Tomé', 32427),
 ("St. John's", 32441),
 ('Monaco', 32439),
 ('Belgrade', 32737),
 ('Bandar Seri Begawan', 32431),
 ('Fakaofo', 32427),
 ('Oslo', 32556)]

__2.3. Выберем школы в стране с наибольшим количеством аптек в стлице
и проиндексируем их с помощью R-tree__

In [24]:
query = f'\
node(area:{areaId})["amenity"="school"];\
out geom;'

result = overpass.query(query, timeout=3600)

EPS = 0.000001
idx = index.Rtree()

school_ids = []
school_points = []
for i in range(result.countElements()):
    school_id = result.elements()[i].id()
    school_ids.append(school_id)
    
    geom = result.elements()[i].geometry()
    if (geom != None):
        lon = result.elements()[i].geometry().coordinates[0]
        lat = result.elements()[i].geometry().coordinates[1]
        idx.insert(school_id, (lon - EPS, lat + EPS, lon + EPS, lat + EPS))

        school_points.append(Point(lat, lon))

school_df = gpd.GeoDataFrame(zip(school_ids, school_points,[0] * len(school_ids)), 
                          columns=['ids','geometry','distance'],
                          geometry='geometry',
                          crs={'init': 'epsg:4326'})
school_df

C:\ProgramData\Anaconda3\envs\made-geo\lib\site-packages\pyproj\crs\crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))


ids                     geometry  distance
0       259201773   POINT (-1.06706 -46.76286)         0
1       262553369   POINT (-1.04904 -46.76641)         0
2       301443881   POINT (-1.07760 -46.76282)         0
3       321706729  POINT (-19.34242 -43.65307)         0
4       336116159  POINT (-19.82746 -40.36151)         0
...           ...                          ...       ...
13596  8068946699  POINT (-29.66288 -53.85808)         0
13597  8072446495  POINT (-12.96808 -38.49804)         0
13598  8074943608  POINT (-29.17247 -51.15191)         0
13599  8077406646  POINT (-18.58013 -57.51409)         0
13600  8081823571  POINT (-14.68855 -42.37890)         0

[13601 rows x 3 columns]

__2.4. Найдем ближайшие школы и расстояние до них для точки из Афганистана__

In [25]:
nearest_ids = list(idx.nearest((TASK2_POINT.y, TASK2_POINT.x, TASK2_POINT.y, TASK2_POINT.x), 5))

school_nearest = school_df.loc[school_df['ids'].isin(nearest_ids)]
for i in school_nearest.index :
    school_pt = school_nearest.loc[i, 'geometry']
    d = haversine((TASK2_POINT.x, TASK2_POINT.y), (school_pt.x, school_pt.y))
    school_nearest.loc[i, 'distance'] = d
    
print("Пять ближайших к точке в Афганистан школ в Бразилии")
school_nearest


Пять ближайших к точке в Афганистан школ в Бразилии


C:\ProgramData\Anaconda3\envs\made-geo\lib\site-packages\pandas\core\indexing.py:1765: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  isetter(loc, value)


ids                    geometry      distance
72      503357179  POINT (-5.77553 -35.19791)  11510.476728
76      506577202  POINT (-5.79481 -35.18882)  11510.947392
3849   3075210276  POINT (-5.88364 -35.17270)  11515.403668
3979   3187807052  POINT (-5.67412 -35.21874)  11505.600452
11713  6790217684  POINT (-5.79040 -35.20035)  11511.678592

## Задание №3. Поездка по Нью-Йорку (маршрут - 20 баллов, визуализация - 10 баллов).

Добраться __на автомобиле__ от входа в ``Central Park`` __Нью-Йорка__ (со стороны ``5th Avenue``) до пересечения ``Water Street`` и ``Washington Street`` в Бруклине (откуда получаются лучшие фото Манхэттенского моста) довольно непросто - разумеется, из-за вечных пробок. Однако еще сложнее это сделать, проезжая мимо школ, где дети то и дело переходят дорогу в неположенном месте.

Вам необходимо построить описанный выше маршрут, избегая на своем пути школы. Визуализируйте данный маршрут (также добавив школы и недоступные для проезда участки дорог) при помощи ``Folium``

Данные о расположении школ Нью-Йорка можно найти [здесь](https://catalog.data.gov/dataset/2019-2020-school-point-locations)

In [26]:
import pandas as pd
import geopandas as gpd
import numpy as np
import folium

from shapely.geometry import Point, LineString, Polygon, MultiPolygon, mapping
from OSMPythonTools.overpass import Overpass, overpassQueryBuilder
from OSMPythonTools.nominatim import Nominatim
from openrouteservice import client

overpass = Overpass()
nominatim = Nominatim()

api_key = '5b3ce3597851110001cf62488a006e3bbc754c09bfef5e9bf2e41bb7'
orsclient = client.Client(key=api_key)

ROUTE_BUFFER_SIZE = 0.05
SCHOOL_BUFFER_SIZE = 0.00075


__1. Найдем начальную и конечную точки маршрута:__
- начальная - пересечение 5th Avenue и East 66th Street (у входа в Центральный зоопарк, там кстати школа рядом)
- конечная - пересечение Water Street и Washington Street

In [28]:
nyAreaId = nominatim.query('New York, USA').areaId()
print(f"New York AreaId = {nyAreaId}")

query = \
f'way(area:{nyAreaId})[name="5th Avenue"]->.w1;\
  way(area:{nyAreaId})[name="East 66th Street"]->.w2;\
  node(w.w1)(w.w2);\
  out body;\
  way(area:{nyAreaId})[name="Water Street"]->.w1;\
  way(area:{nyAreaId})[name="Washington Street"]->.w2;\
  node(w.w1)(w.w2);\
  out body;'

result = overpass.query(query)
startPoint = result.elements()[0].geometry().coordinates
endPoint = result.elements()[1].geometry().coordinates

print(f"Start point: {startPoint}")
print(f"End point: {endPoint}")

New York AreaId = 3600175905
Start point: [-73.969825, 40.768646]
End point: [-73.98958, 40.703201]


__Пробуем создать наикратчайший маршрут__

In [29]:
centerPoint = [(startPoint[1] + endPoint[1]) / 2, (startPoint[0] + endPoint[0]) / 2]
route_map_shortest = folium.Map(location=centerPoint, zoom_start=13)

request_params = {'coordinates': [startPoint, endPoint],
                  'profile': 'driving-car', 'format_out': 'geojson',
                  'preference': 'shortest', 'geometry': 'true'}
route_shortest = orsclient.directions(**request_params)

__Визуализация кратчайшего маршрута__

In [30]:
folium.features\
.GeoJson(data=route_shortest,name='Shortest rout')\
.add_to(route_map_shortest)

folium.Marker(
    location=(startPoint[1], startPoint[0]),
    popup=f"Start",
    icon=folium.Icon(color='blue')
).add_to(route_map_shortest)

folium.Marker(
    location=(endPoint[1], endPoint[0]),
    popup=f"End",
    icon=folium.Icon(color='blue')
).add_to(route_map_shortest)

route_map_shortest

__2. Собираю данные по школам в Манхэттене и Бруклине__

In [32]:
manhAreaId = nominatim.query('Manhattan, New York, USA').areaId()
print(f"Manhattan AreaId = {manhAreaId}")

brooAreaId = nominatim.query('Brooklyn, New York, USA').areaId()
print(f"Brooklyn AreaId = {brooAreaId}")

df = gpd.read_file('NY_Schools.geojson')

Manhattan AreaId = 3608398124
Brooklyn AreaId = 3609691750


'NY_Schools.geojson' экспортировал через Overpass: https://overpass-turbo.eu/s/ZIu \

`node(area:{manhAreaId})["amenity"="school"];
out geom;
node(area:{brooAreaId})["amenity"="school"];
out geom;`

__Для создания маршрута, учитывающего расположение школ понадобится буферный полигон__

In [33]:
route_shortest_coords = route_shortest['features'][0]['geometry']['coordinates']
route_shortest_buffer = LineString(route_shortest_coords).buffer(ROUTE_BUFFER_SIZE)
route_shortest_polygon = Polygon(route_shortest_buffer)

folium.features\
.GeoJson(data=route_shortest_polygon,overlay=True)\
.add_to(route_map_shortest)


__Для каждой школы внутри буферного полигона создаем окрестность__

In [34]:
schools_geom = df['geometry']

schools_points = [pt for pt in schools_geom if pt.within(route_shortest_buffer)]

schools_areas = []
for pt in schools_points:
    pt_poly = pt.buffer(SCHOOL_BUFFER_SIZE)
    schools_areas.append(pt_poly)

schools_polygon = MultiPolygon(schools_areas)

schools_style_func = lambda x: dict(color='orange', opacity=0.5)

folium.features\
.GeoJson(data=schools_polygon,overlay=True,
         style_function=schools_style_func)\
.add_to(route_map_shortest)

for pt in schools_points:
    folium.Marker(location=(pt.y, pt.x),
        popup="School",icon=folium.Icon(color='orange'))\
    .add_to(route_map_shortest)

route_map_shortest

__3. Создаем маршрут, учитывающий расположение школ__

In [35]:
request_params['options'] = { 'avoid_polygons': mapping(schools_polygon) }
route_faster = orsclient.directions(**request_params)

route_style_func = lambda x: dict(color='green')

folium.features\
.GeoJson(data=route_faster,name='Faster route', style_function=route_style_func)\
.add_to(route_map_shortest)
route_map_shortest